In [1]:
import pandas as pd
import numpy as np
import clean_df as cd

/Users/loremipsum/Documents/GitHub/company_cleaning/.venv/lib/python3.10/site-packages/fuzzywuzzy/fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [2]:
df = pd.read_csv('ndc.csv')
df = df.dropna()
print(df)
df['name'] = df['name'].str.lower()
print(len(set(df['name'])))

                              name
0                       Row Labels
1                SPIRONOLACTONE % 
2        -L'Oreal USA Products Inc
3                 .Cardinal Health
4     .Church & Dwight Canada Corp
...                            ...
7022                        ZYGONE
7023    Zyla Life Sciences US Inc.
7024                        #NAME?
7025                       (blank)
7026                   Grand Total

[7027 rows x 1 columns]
6701


In [3]:
df['clean'] = df['name'].map(cd.clean_str)
print(df)
print(len(set(df['clean'])))

                              name                      clean
0                       row labels                 row labels
1                spironolactone %              spironolactone
2        -l'oreal usa products inc    loreal usa products inc
3                 .cardinal health            cardinal health
4     .church & dwight canada corp  church dwight canada corp
...                            ...                        ...
7022                        zygone                     zygone
7023    zyla life sciences us inc.  zyla life sciences us inc
7024                        #name?                       name
7025                       (blank)                      blank
7026                   grand total                grand total

[7027 rows x 2 columns]
5787


In [4]:
df['-company'] = df['clean'].map(cd.filter_company_name)
print(df)
print(len(set(df['-company'])))

                              name                      clean  \
0                       row labels                 row labels   
1                spironolactone %              spironolactone   
2        -l'oreal usa products inc    loreal usa products inc   
3                 .cardinal health            cardinal health   
4     .church & dwight canada corp  church dwight canada corp   
...                            ...                        ...   
7022                        zygone                     zygone   
7023    zyla life sciences us inc.  zyla life sciences us inc   
7024                        #name?                       name   
7025                       (blank)                      blank   
7026                   grand total                grand total   

                  -company  
0               row labels  
1           spironolactone  
2          loreal products  
3          cardinal health  
4     church dwight canada  
...                    ...  
7022            

In [5]:
states = cd.prep_states_info()

In [6]:
df['-states'] = df['-company'].apply(lambda x: cd.filter_states_info(x, states))
print(df)
print(len(set(df['-states'])))

                              name                      clean  \
0                       row labels                 row labels   
1                spironolactone %              spironolactone   
2        -l'oreal usa products inc    loreal usa products inc   
3                 .cardinal health            cardinal health   
4     .church & dwight canada corp  church dwight canada corp   
...                            ...                        ...   
7022                        zygone                     zygone   
7023    zyla life sciences us inc.  zyla life sciences us inc   
7024                        #name?                       name   
7025                       (blank)                      blank   
7026                   grand total                grand total   

                  -company               -states  
0               row labels            row labels  
1           spironolactone        spironolactone  
2          loreal products       loreal products  
3          card

In [7]:
common_words = cd.get_words()
df['-common'] = df['-states'].apply(lambda x: cd.filter_common_words(x, common_words))
print(df.columns)

Index(['name', 'clean', '-company', '-states', '-common'], dtype='object')


In [8]:
df['short'] = df.apply(lambda row: cd.get_shortest_non_empty(row['name'], row['clean'], row['-company'], row['-states'], row['-common']), axis=1)

In [9]:
print('products' in common_words)
print('supply' in common_words)
print('welding' in common_words)
print('a' in common_words)

False
True
True
True


In [10]:
pd.set_option('display.max_rows', None)
display(df)
pd.reset_option('display.max_rows')

name  \
0                                            row labels   
1                                     spironolactone %    
2                             -l'oreal usa products inc   
3                                      .cardinal health   
4                          .church & dwight canada corp   
5                         {preferred pharmaeutials inc.   
6                               †wal-mart stores, inc.†   
7                                       veterans health   
8                                                 medco   
9                        st class pharmaceuticals, inc.   
10                                          st medx llc   
11                                            transform   
12                  st century designer health products   
13                              st century homeopathics   
14                         st century homeopathics, inc   
15                                       xl corporation   
16                                          innovations   
17            d imaging drug design and development llc   
18                                                  lab   
19                                             lab, inc   
20                                            lab, inc.   
21                                            m company   
22                               m espe dental products   
23                                        m health care   
24                            e brands northamerica llc   
25                            e global, s.a.p.i. de c.v   
26                               life research usa, llc   
27                                         sport d.o.o.   
28                                           senco inc.   
29                         degrees pharmaceuticals, llc   
30                                                    -   
31                                               c, llc   
32                                              -eleven   
33                                          -eleven inc   
34                                         -eleven inc.   
35                                        -eleven, inc.   
36                                       essentials ltd   
37                                         t pharma llc   
38                       . ideal balance d.o.o. beograd   
39                                                 corp   
40                             a & b welding supply co.   
41                    a & d healthcare equipment repair   
42                  a & e mill & welding supply company   
43                                  a + oxygen & d.m.e.   
44                     a ox welding supply company inc.   
45                                  a plus home medical   
46                            a-cute derm, incorporated   
47                        a-ox welding supply co., inc.   
48                             a-s medication solutions   
49                    a-welders and medical supply, inc   
50                                  a.p. deauville, llc   
51                             a.t.s. laboratories, llc   
52                          a&z holistic products, inc.   
53                              a&z pharmaceutical inc.   
54                             a&z pharmaceutical, inc.   
55                                               a, llc   
56                   aa integrated pharmaceuticals, llc   
57                                     az products, llc   
58                             aaa pharmaceutical, inc.   
59                           aace pharmaceuticals, inc.   
60                                                aafes   
61                        aavishkar oral strips pvt ltd   
62                      aavishkar oral strips pvt. ltd.   
63              aaxis pacific dba aaxis pharmaceuticals   
64          aaxis pharmaceuticals inc dba aaxis pacific   
65                       abaco partners llc dba surefil   
66                              abbe laboratories, inc.   
67                                     

In [11]:
total_companies = set(df['short'])
print(df[df['short'] == '-'])
print(len(total_companies))

   name clean -company -states -common short
30    -                                    -
5375


In [12]:
ndf = pd.DataFrame()
ndf['name'] = sorted(list(total_companies))
print(ndf)

                                 name
0                                   -
1                                   a
2                  a b welding supply
3     a d healthcare equipment repair
4             a e mill welding supply
...                               ...
5370    zunyi jici biohealth products
5371                    zydus limited
5372            zydus pharmaceuticals
5373                           zygone
5374                     zyla life us

[5375 rows x 1 columns]


In [13]:
ndf.to_csv('ndf_cleaned.csv', index=False)
print('%.2f reduction' % ((len(df)-len(ndf))/len(df)))

0.24 reduction
